# Potato Chip Analysis

### Made by Alejandro Nadal. The datasets are from Quantium 

Here we will be working with two datasets, one of customers, the other of transactions of potato chips. We will try to derive some conclusions and give some recomendations for our clients. First, lets describe the two datasets and its parts

QVI_purchase_behaviour.csv contains the **card number**, **lifestage**, and **premium_customer**. Let's see the possible values

In [55]:
import numpy as np
import pandas_profiling as pp
import itertools
from sklearn.preprocessing import LabelEncoder

In [32]:
import pandas as pd

clients = pd.read_csv("QVI_purchase_behaviour.csv")

print(clients)

       LYLTY_CARD_NBR               LIFESTAGE PREMIUM_CUSTOMER
0                1000   YOUNG SINGLES/COUPLES          Premium
1                1002   YOUNG SINGLES/COUPLES       Mainstream
2                1003          YOUNG FAMILIES           Budget
3                1004   OLDER SINGLES/COUPLES       Mainstream
4                1005  MIDAGE SINGLES/COUPLES       Mainstream
...               ...                     ...              ...
72632         2370651  MIDAGE SINGLES/COUPLES       Mainstream
72633         2370701          YOUNG FAMILIES       Mainstream
72634         2370751          YOUNG FAMILIES          Premium
72635         2370961          OLDER FAMILIES           Budget
72636         2373711   YOUNG SINGLES/COUPLES       Mainstream

[72637 rows x 3 columns]


In [33]:
## Now, lets see the possible values of lifestage and premium_customer

lifestage_possible_values=clients.LIFESTAGE.unique()

print(lifestage_possible_values)

premium_customer_possible_values = clients.PREMIUM_CUSTOMER.unique()

print(premium_customer_possible_values)

['YOUNG SINGLES/COUPLES' 'YOUNG FAMILIES' 'OLDER SINGLES/COUPLES'
 'MIDAGE SINGLES/COUPLES' 'NEW FAMILIES' 'OLDER FAMILIES' 'RETIREES']
['Premium' 'Mainstream' 'Budget']


Now, lets load the QVI_transaction_data.xlsx

In [34]:
transactions = pd.read_excel('QVI_transaction_data.xlsx')
print(transactions)

         DATE  STORE_NBR  LYLTY_CARD_NBR  TXN_ID  PROD_NBR  \
0       43390          1            1000       1         5   
1       43599          1            1307     348        66   
2       43605          1            1343     383        61   
3       43329          2            2373     974        69   
4       43330          2            2426    1038       108   
...       ...        ...             ...     ...       ...   
264831  43533        272          272319  270088        89   
264832  43325        272          272358  270154        74   
264833  43410        272          272379  270187        51   
264834  43461        272          272379  270188        42   
264835  43365        272          272380  270189        74   

                                       PROD_NAME  PROD_QTY  TOT_SALES  
0         Natural Chip        Compny SeaSalt175g         2        6.0  
1                       CCs Nacho Cheese    175g         3        6.3  
2         Smiths Crinkle Cut  Chips Chi

Now, let's analyze the fields: the date field is in the Julian Calendar. **LYLTY_CARD_NBR** is the client number. **TXN_ID** is the transaction ID, **PROD_NBR** is the number of the product. **PROD_NAME** does not require much of an explanation. **PROD_QTY** is the number of items bought and **TOT_SALES** is the money earned in that sale.

First, lets find null or empty values, to sanitize the data.

In [35]:
##First, replace every empty string with a NaN, so it is easier to search
transactions = transactions.replace('',np.nan)
clients = clients.replace('',np.nan)

In [36]:
np.where(pd.isnull(clients))
np.where(pd.isnull(transactions))

(array([], dtype=int64), array([], dtype=int64))

It would seem that there were no null or empty values of any kind. Now, lets start to analyze the dataframes

Summarize dataset:   0%|          | 0/21 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

Nice! So much information. Some essential things we must do with our data before merging transactions with our client data, is to solve a duplicate row, and some outliers: Transaction ID 2415841, a transaction where 200 potato chip were sold, and transaction where $650 dollars were earned. Let's look for those

In [38]:
duplicatedTransactions = transactions[transactions.duplicated()]

In [39]:
print(duplicatedTransactions.index[0])

124845


In [40]:
rows_to_eliminate=[]
rows_to_eliminate.append(duplicatedTransactions.index.values.tolist())

In [41]:
transactions[transactions['TOT_SALES'].gt(649)]

DATE  STORE_NBR  LYLTY_CARD_NBR  TXN_ID  PROD_NBR  \
69762  43331        226          226000  226201         4   
69763  43605        226          226000  226210         4   

                              PROD_NAME  PROD_QTY  TOT_SALES  
69762  Dorito Corn Chp     Supreme 380g       200      650.0  
69763  Dorito Corn Chp     Supreme 380g       200      650.0

It seems that both of our outliers on PROD_QTY and TOT_SALES are in those rows, so we add them to be deleted

In [42]:
rows_to_eliminate.append(transactions[transactions['TOT_SALES'].gt(649)].index.values.tolist())

Last but not least, the row with a huge transaction number

In [43]:
transactions[transactions['TXN_ID'].eq(2415841)]

DATE  STORE_NBR  LYLTY_CARD_NBR   TXN_ID  PROD_NBR  \
15726  43454         88          237324  2415841       102   

                                    PROD_NAME  PROD_QTY  TOT_SALES  
15726  Kettle Mozzarella   Basil & Pesto 175g         2       10.8

In [44]:
rows_to_eliminate.append(transactions[transactions['TXN_ID'].eq(2415841)].index.values.tolist())

In [45]:
rows_to_eliminate
flat_list = []

In [46]:
for subr in rows_to_eliminate:
    for item in subr:
        flat_list.append(item)
flat_list

[124845, 69762, 69763, 15726]

Now, let's delete these bothersome rows

In [47]:
transactions.drop(index=flat_list, inplace=True)

In [48]:
transactions

DATE  STORE_NBR  LYLTY_CARD_NBR  TXN_ID  PROD_NBR  \
0       43390          1            1000       1         5   
1       43599          1            1307     348        66   
2       43605          1            1343     383        61   
3       43329          2            2373     974        69   
4       43330          2            2426    1038       108   
...       ...        ...             ...     ...       ...   
264831  43533        272          272319  270088        89   
264832  43325        272          272358  270154        74   
264833  43410        272          272379  270187        51   
264834  43461        272          272379  270188        42   
264835  43365        272          272380  270189        74   

                                       PROD_NAME  PROD_QTY  TOT_SALES  
0         Natural Chip        Compny SeaSalt175g         2        6.0  
1                       CCs Nacho Cheese    175g         3        6.3  
2         Smiths Crinkle Cut  Chips Chicken 170g         2        2.9  
3         Smiths Chip Thinly  S/Cream&Onion 175g         5       15.0  
4       Kettle Tortilla ChpsHny&Jlpno Chili 150g         3       13.8  
...                                          ...       ...        ...  
264831   Kettle Sweet Chilli And Sour Cream 175g         2       10.8  
264832             Tostitos Splash Of  Lime 175g         1        4.4  
264833                  Doritos Mexicana    170g         2        8.8  
264834   Doritos Corn Chip Mexican Jalapeno 150g         2        7.8  
264835             Tostitos Splash Of  Lime 175g         2        8.8  

[264832 rows x 8 columns]

In [49]:
##Saving pd to csv to avoid calculating all these again
transactions.to_csv('transactions_corrected.csv', index=False)

Now let's do the same analysis to check the clients file

In [50]:
pp.ProfileReport(df=clients, minimal=False)

Summarize dataset:   0%|          | 0/16 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

Well, there seems to be no need for changes on the clients data, so, let's merge the files, using the merge operation 

In [51]:
dataset = pd.merge(transactions, clients, on='LYLTY_CARD_NBR', how='left')

Let's now perform a simple, exploratory analysis on the full dataset, to check if the merge operation left us with non existing clients, and to see any tendencies that we can check on.

In [52]:
exploratory_report =pp.ProfileReport(df=dataset,minimal=False, explorative = True)

In [61]:
dataset_m = dataset.copy()

In [62]:
le=LabelEncoder()
dataset_m["LABEL_CLIENT_CAT"]=le.fit_transform(dataset_m["PREMIUM_CUSTOMER"])

In [68]:
exploratory_report2 = pp.ProfileReport(df=dataset_m,minimal=False,explorative=True)

In [70]:
exploratory_report2

Summarize dataset:   0%|          | 0/24 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]